# Intelligent Agents: Reflex-Based Agents for the Vacuum-cleaner World


## Instructions

Total Points: Undergrads 100 / Graduate students 110

Complete this notebook. Use the provided notebook cells and insert additional code and markdown cells as needed. Submit the completely rendered notebook as a PDF file. 

## Introduction

In this assignment you will implement a simulator environment for an automatic vacuum cleaner robot, a set of different reflex-based agent programs, and perform a comparison study for cleaning a single room. Focus on the __cleaning phase__ which starts when the robot is activated and ends when the last dirty square in the room has been cleaned. Someone else will take care of the agent program needed to navigate back to the charging station after the room is clean.

## PEAS description of the cleaning phase

__Performance Measure:__ Each action costs 1 energy unit. The performance is measured as the sum of the energy units used to clean the whole room.

__Environment:__ A room with $n \times n$ squares where $n = 5$. Dirt is randomly placed on each square with probability $p = 0.2$. For simplicity, you can assume that the agent knows the size and the layout of the room (i.e., it knows $n$). To start, the agent is placed on a random square.

__Actuators:__ The agent can clean the current square (action `suck`) or move to an adjacent square by going `north`, `east`, `south`, or `west`.

__Sensors:__ Four bumper sensors, one for north, east, south, and west; a dirt sensor reporting dirt in the current square.  


## The agent program for a simple randomized agent

The agent program is a function that gets sensor information (the current percepts) as the arguments. The arguments are:

* A dictionary with boolean entries for the for bumper sensors `north`, `east`, `west`, `south`. E.g., if the agent is on the north-west corner, `bumpers` will be `{"north" : True, "east" : False, "south" : False, "west" : True}`.
* The dirt sensor produces a boolean.

The agent returns the chosen action as a string.

Here is an example implementation for the agent program of a simple randomized agent:  

In [1]:
import numpy as np

actions = ["north", "east", "west", "south", "suck"]

def simple_randomized_agent(bumpers, dirty):
    return np.random.choice(actions)

In [2]:
# define percepts (current location is NW corner and it is dirty)
bumpers = {"north" : True, "east" : False, "south" : False, "west" : True}
dirty = True

# call agent program function with percepts and it returns an action
simple_randomized_agent(bumpers, dirty)

'east'

__Note:__ This is not a rational intelligent agent. It ignores its sensors and may bump into a wall repeatedly or not clean a dirty square. You will be asked to implement rational agents below.

## Simple environment example

We implement a simple simulation environment that supplies the agent with its percepts.
The simple environment is infinite in size (bumpers are always `False`) and every square is always dirty, even if the agent cleans it. The environment function returns a performance measure which is here the number of cleaned squares (since the room is infinite and all squares are constantly dirty, the agent can never clean the whole room as required in the PEAS description above). The energy budget of the agent is specified as `max_steps`. 

In [3]:
def simple_environment(agent, max_steps, verbose = True):
    num_cleaned = 0
    
    for i in range(max_steps):
        dirty = True
        bumpers = {"north" : False, "south" : False, "west" : False, "east" : False}

        action = agent(bumpers, dirty)
        if (verbose): print("step", i , "- action:", action) 
        
        if (action == "suck"): 
            num_cleaned = num_cleaned + 1
        
    return num_cleaned
        


Do one simulation run with a simple randomized agent that has enough energy for 20 steps.

In [4]:
simple_environment(simple_randomized_agent, max_steps = 20)

step 0 - action: suck
step 1 - action: south
step 2 - action: west
step 3 - action: west
step 4 - action: suck
step 5 - action: suck
step 6 - action: suck
step 7 - action: suck
step 8 - action: north
step 9 - action: east
step 10 - action: south
step 11 - action: south
step 12 - action: west
step 13 - action: north
step 14 - action: suck
step 15 - action: north
step 16 - action: suck
step 17 - action: west
step 18 - action: east
step 19 - action: north


7

# Tasks

## General [10 Points]

1. Make sure that you use the latest version of this notebook. Sync your forked repository and pull the latest revision. 
2. Your implementation can use libraries like math, numpy, scipy, but not libraries that implement inteligent agents or complete search algorithms. Try to keep the code simple! In this course, we want to learn about the algorithms and we often do not need to use object-oriented design.
3. You notebook needs to be formated professionally. 
    - Add additional markdown blocks for your description, comments in the code, add tables and use mathplotlib to produce charts where appropriate
    - Do not show debugging output or include an excessive amount of output.
    - Check that your PDF file is readable. For example, long lines are cut off in the PDF file. You don't have control over page breaks, so do not worry about these.
4. Document your code. Add a short discussion of how your implementation works and your design choices.


## Task 1: Implement a simulation environment [20 Points]

The simple environment above is not very realistic. Your environment simulator needs to follow the PEAS description from above. It needs to:

* Initialize the environment by storing the state of each square (clean/dirty) and making some dirty. ([Help with random numbers and arrays in Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/random_numbers_and_arrays.ipynb))
* Keep track of the agent's position.
* Call the agent function repeatedly and provide the agent function with the sensor inputs.  
* React to the agent's actions. E.g, by removing dirt from a square or moving the agent around unless there is a wall in the way.
* Keep track of the performance measure. That is, track the agent's actions until all dirty squares are clean and count the number of actions it takes the agent to complete the task.

The easiest implementation for the environment is to hold an 2-dimensional array to represent if squares are clean or dirty and to call the agent function in a loop until all squares are clean or a predefined number of steps have been reached (i.e., the robot runs out of energy).

The simulation environment should be a function like the `simple_environment()` and needs to work with the simple randomized agent program from above. **Use the same environmnt for all your agent implementations in the tasks below.**

*Note on debugging:* Debugging is difficult. Make sure your environment prints enough information when you use `verbose = True`. Also, implementing a function that the environment can use to displays the room with dirt and the current position of the robot at every step is very useful.  

## Bumper Sensors


<div class="alert alert-block alert-info">
<b>Bumper Sensors</b> The bumper sensors identify whether the vacuum has a reached a wall or a corner based on its location. The default value is set as false and is returned unless if the bumpers are activated by a specific location.

I made these sensors a separate function that returns the bumpers to the simulation environment when called.
    
    
**Worth noting:** Bumpers that are strictly one direction (i.e. just north) mean that the vacuum hit a wall but not a corner.
</div>

In [5]:
def bumper_sensors(n, position_x, position_y):
    
    bumpers = {"north": False, "south": False, "west": False, "east": False}
    
    # If East
    if(position_x == n-1):
        # If Northeast
        if(position_y == 0):
            return {"north" : True, "south" : False, "west" : False, "east" : True}
        
        # If Southeast
        elif(position_y == n-1):
            return {"north" : False, "south" : True, "west" : False, "east" : True}
        
        # If Only East
        else:
            return {"north" : False, "south" : False, "west" : False, "east" : True}
    
    # If West
    elif(position_x == 0):
        if(position_y == 0):
            return {"north" : True, "south" : False, "west" : True, "east" : False}
        elif(position_y == n-1):
            return {"north" : False, "south" : True, "west" : True, "east" : False}
        else:
            return{ "north" : False, "south" : False, "west" : True, "east" : False}
    
    # If only North or only South
    if(position_y == 0):
        return {"north" : True, "south" : False, "west" : False, "east" : False}
    elif(position_y == n-1):
        return{"north" : False, "south" : True, "west" : False, "east" : False}

    return bumpers

### Simulation Environment

To summarize the simulation environment I created, it essentially creates the environment with nxn number of squares. It generates a random starting position for the agent used and also assigns a random assortment of squares as either clean or dirty (clean = True, dirty = False). From there, it reacts to the actions outputted by the agent by either cleaning, staying if the square is already clean, or moving to the next square in the direction the agent indicates.

This simulation environment runs until the entire room is clean.


#### The Simulation Environment I created keeps track of the following things:
1. Number of dirty squares
2. Starting position of vacuum
3. Bumper sensors
4. Dirt sensors
5. Total number of squares cleaned 
6. **Performance Measure:** Total number of actions (1 action = 1 energy unit)Total number of squares cleaned 

In [6]:
# Your code and description goes here
def simulation_environment(agent, n): 
    num_cleaned = 0 # Keeping track of swaures cleaned
    num_actions_total = 0
    rng = np.random.default_rng() # create random number generator
    p = 0.2 # use given probability from instructions
    squares = [[rng.random() < p for x in range(n)] for y in range(n)] # intitalize squares array w/ clean and dirty squares
    count_dirty = np.count_nonzero(squares)
    print("Number of dirty squares:")
    print(count_dirty)
    position_x = rng.integers(low = 0, high = n-1)
    position_y = rng.integers(low = 0, high = n-1)
    dirty = squares[position_x][position_y]
    bumpers = bumper_sensors(n, position_x, position_y)
    print(bumpers)
    
    while(count_dirty != 0):
        action = agent(bumpers, dirty)
        
        if (action == "suck" and squares[position_x][position_y] == True):
            squares[position_x][position_y] = False
            num_cleaned = num_cleaned + 1
            count_dirty = np.count_nonzero(squares)
        elif (action == "suck" and squares[position_x][position_y] == False):
            action = "already clean - stay in position"
        
        if (verbose): print("Environment: Step", num_actions_total , "- action:", action, " position: (", position_x, ",", position_y, ")")
        num_actions_total += 1

        if(action == "west"):
            position_x -= 1
            if(position_x < 0):
                position_x = 0
            
        if(action == "east"):
            position_x += 1
            if(position_x > n-1):
                position_x = n-1
            

        if(action == "north"):
            position_y -= 1
            if(position_y < 0):
                position_y = 0
                
        if(action == "south"):
            position_y += 1
            if(position_y > n-1):
                position_y = n-1
        
        
            
        dirty = squares[position_x][position_y]
        bumpers = bumper_sensors(n, position_x, position_y)
        
    print("Total number of actions: ")
    print(num_actions_total)
    for i in range(n):
        print(squares[i])

    print("Final Position - (", position_x, ",", position_y, ")")
    print("Number of squares cleaned: ", num_cleaned)    
    print("Total energy units used:")
    return num_actions_total
        
    


In [7]:
simulation_environment(simple_randomized_agent, 5)

Number of dirty squares:
2
{'north': False, 'south': False, 'west': False, 'east': False}
Environment: Step 0 - action: south  position: ( 3 , 3 )
Environment: Step 1 - action: already clean - stay in position  position: ( 3 , 4 )
Environment: Step 2 - action: west  position: ( 3 , 4 )
Environment: Step 3 - action: south  position: ( 2 , 4 )
Environment: Step 4 - action: west  position: ( 2 , 4 )
Environment: Step 5 - action: north  position: ( 1 , 4 )
Environment: Step 6 - action: north  position: ( 1 , 3 )
Environment: Step 7 - action: north  position: ( 1 , 2 )
Environment: Step 8 - action: south  position: ( 1 , 1 )
Environment: Step 9 - action: north  position: ( 1 , 2 )
Environment: Step 10 - action: north  position: ( 1 , 1 )
Environment: Step 11 - action: east  position: ( 1 , 0 )
Environment: Step 12 - action: south  position: ( 2 , 0 )
Environment: Step 13 - action: west  position: ( 2 , 1 )
Environment: Step 14 - action: already clean - stay in position  position: ( 1 , 1 )


Environment: Step 142 - action: west  position: ( 1 , 3 )
Environment: Step 143 - action: already clean - stay in position  position: ( 0 , 3 )
Environment: Step 144 - action: west  position: ( 0 , 3 )
Environment: Step 145 - action: already clean - stay in position  position: ( 0 , 3 )
Environment: Step 146 - action: south  position: ( 0 , 3 )
Environment: Step 147 - action: south  position: ( 0 , 4 )
Environment: Step 148 - action: south  position: ( 0 , 4 )
Environment: Step 149 - action: west  position: ( 0 , 4 )
Environment: Step 150 - action: north  position: ( 0 , 4 )
Environment: Step 151 - action: south  position: ( 0 , 3 )
Environment: Step 152 - action: west  position: ( 0 , 4 )
Environment: Step 153 - action: west  position: ( 0 , 4 )
Environment: Step 154 - action: west  position: ( 0 , 4 )
Environment: Step 155 - action: north  position: ( 0 , 4 )
Environment: Step 156 - action: east  position: ( 0 , 3 )
Environment: Step 157 - action: south  position: ( 1 , 3 )
Environme

Environment: Step 316 - action: north  position: ( 1 , 2 )
Environment: Step 317 - action: east  position: ( 1 , 1 )
Environment: Step 318 - action: west  position: ( 2 , 1 )
Environment: Step 319 - action: west  position: ( 1 , 1 )
Environment: Step 320 - action: already clean - stay in position  position: ( 0 , 1 )
Environment: Step 321 - action: east  position: ( 0 , 1 )
Environment: Step 322 - action: already clean - stay in position  position: ( 1 , 1 )
Environment: Step 323 - action: east  position: ( 1 , 1 )
Environment: Step 324 - action: north  position: ( 2 , 1 )
Environment: Step 325 - action: south  position: ( 2 , 0 )
Environment: Step 326 - action: already clean - stay in position  position: ( 2 , 1 )
Environment: Step 327 - action: north  position: ( 2 , 1 )
Environment: Step 328 - action: south  position: ( 2 , 0 )
Environment: Step 329 - action: north  position: ( 2 , 1 )
Environment: Step 330 - action: west  position: ( 2 , 0 )
Environment: Step 331 - action: south  p

464

## Task 2:  Implement a simple reflex agent [10 Points] 

The simple reflex agent randomly walks around but reacts to the bumper sensor by not bumping into the wall and to dirt with sucking. Implement the agent program as a function.

_Note:_ Agents cannot directly use variable in the environment. They only gets the percepts as the arguments to the agent function.

In [8]:
# Your code and description goes here
def simple_reflex_agent(bumpers, dirty):
    if(dirty == True):
        print("\tAgent: Found a dirty square... GROSS... Cleaning now")
        return "suck" # return suck
    if(bumpers.get("north") == True):
        print("\tAgent: Hit the north wall, will move away now...")
        return "south"
    if(bumpers.get("south") == True):
        print("\tAgent: Hit the south wall, will move away now...")
        return "north"
    if(bumpers.get("east") == True):
        print("\tAgent: Hit the east wall, will move away now...")
        return "west"
    if(bumpers.get("west") == True):
        print("\tAgent: Hit the west wall, will move away now...")
        return "east"

    return np.random.choice(actions)

In [9]:
simulation_environment(simple_reflex_agent, 5)

Number of dirty squares:
5
{'north': True, 'south': False, 'west': False, 'east': False}
	Agent: Hit the north wall, will move away now...
Environment: Step 0 - action: south  position: ( 2 , 0 )
Environment: Step 1 - action: south  position: ( 2 , 1 )
Environment: Step 2 - action: north  position: ( 2 , 2 )
Environment: Step 3 - action: north  position: ( 2 , 1 )
	Agent: Hit the north wall, will move away now...
Environment: Step 4 - action: south  position: ( 2 , 0 )
Environment: Step 5 - action: west  position: ( 2 , 1 )
Environment: Step 6 - action: north  position: ( 1 , 1 )
	Agent: Found a dirty square... GROSS... Cleaning now
Environment: Step 7 - action: suck  position: ( 1 , 0 )
	Agent: Hit the north wall, will move away now...
Environment: Step 8 - action: south  position: ( 1 , 0 )
Environment: Step 9 - action: already clean - stay in position  position: ( 1 , 1 )
Environment: Step 10 - action: south  position: ( 1 , 1 )
	Agent: Found a dirty square... GROSS... Cleaning now


104

## Task 3: Implement a model-based reflex agent [20 Points]

Model-based agents use a state to keep track of what they have done and perceived so far. Your agent needs to find out where it is located and then keep track of its current location. You also need a set of rules based on the state and the percepts to make sure that the agent will clean the whole room. For example, the agent can move to a corner to determine its location and then it can navigate through the whole room and clean dirty squares.

Describe how you define the __agent state__ and how your agent works before implementing it. ([Help with implementing state information on Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/store_agent_state_information.ipynb))

In [10]:
# Your short description of the state and your implementation goes here
# Going into the room, the agent will assume that the entire room is dirty...


In [11]:
phase_one = False
cleaned = []
row = -1
col = -1
direction = "east"

def Model_Based_Reflex(bumpers, dirty):
    global phase_one
    global direction
    global clean
    global row
    global col

    if(phase_one == False):
        if(bumpers.get("north") == True and bumpers.get("west") == True):
            phase_one = True
            print("\tAgent: Position 0 Reached! Phase One Complete. Will now begin Phase 2: Cleaning.")
            row = 0
            col = 0
            if(dirty):
                print("\tAgent: Found a dirty square... GROSS... Cleaning now")
                return "suck"
            else: 
                print("\tAgent: Moving to next corner!")
                return "east"
        if(bumpers.get("north") == False):
            print("\tAgent: Moving to Position 0 (Northwest Corner)\n\tMoving...")
            return "north"
        elif(bumpers.get("west") == False):
            print("\tAgent: Moving to Position 0 (Northwest Corner)\n\tMoving...")
            return "west"

    else: 
        if(dirty):
            print("\tAgent: Found a dirty square... GROSS... Cleaning now")
            cleaned.append([row, col])
            return "suck"
        else:
            if(not(bumpers.get(direction))):
                if(direction == "east"):
                    print("\tAgent: Moving to east wall")
                    col += 1
                else:
                    print("\tAgent: Moving to west wall")
                    col -= 1
                return direction
            else:
                if(direction == "east"):
                    print("\tAgent: Wall reached! Moving south and continuing west.")
                    direction = "west"
                else:
                    print("\tAgent: Wall reached! Moving south and continuing east.")
                    direction = "east"
                row += 1
                return "south"


    

        moving = True

In [12]:
simulation_environment(Model_Based_Reflex, 5)

Number of dirty squares:
1
{'north': False, 'south': False, 'west': False, 'east': False}
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 0 - action: north  position: ( 2 , 1 )
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 1 - action: west  position: ( 2 , 0 )
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 2 - action: west  position: ( 1 , 0 )
	Agent: Position 0 Reached! Phase One Complete. Will now begin Phase 2: Cleaning.
	Agent: Moving to next corner!
Environment: Step 3 - action: east  position: ( 0 , 0 )
	Agent: Moving to east wall
Environment: Step 4 - action: east  position: ( 1 , 0 )
	Agent: Moving to east wall
Environment: Step 5 - action: east  position: ( 2 , 0 )
	Agent: Moving to east wall
Environment: Step 6 - action: east  position: ( 3 , 0 )
	Agent: Wall reached! Moving south and continuing west.
Environment: Step 7 - action: south  position: ( 4 , 0 )
	Agent: Moving to west wall
En

19

## Task 4: Simulation study [30 Points]

Compare the performance (the performance measure is defined in the PEAS description above) of the agents using  environments of different size. E.g., $5 \times 5$, $10 \times 10$ and
$100 \times 100$. Use 100 random runs for each. Present the results using tables and graphs. Discuss the differences between the agents. 
([Help with charts and tables in Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/charts_and_tables.ipynb))

In [13]:
# Your code goes here
import seaborn as sns

In [ ]:
environment_sizes = [5, 10, 100]

simple_random = []
simple_reflex = []
model_reflex = []

for x in range(100):
    n = np.random.choice(environment_sizes)
    simple_random.append([n, simulation_environment(simple_randomized_agent, n)])
    simple_reflex.append([n, simulation_environment(simple_reflex_agent, n)])
    model_reflex.append([n, simulation_environment(Model_Based_Reflex, n)])
    


Number of dirty squares:
21
{'north': False, 'south': False, 'west': False, 'east': False}
Environment: Step 0 - action: north  position: ( 3 , 5 )
Environment: Step 1 - action: east  position: ( 3 , 4 )
Environment: Step 2 - action: west  position: ( 4 , 4 )
Environment: Step 3 - action: south  position: ( 3 , 4 )
Environment: Step 4 - action: east  position: ( 3 , 5 )
Environment: Step 5 - action: north  position: ( 4 , 5 )
Environment: Step 6 - action: north  position: ( 4 , 4 )
Environment: Step 7 - action: already clean - stay in position  position: ( 4 , 3 )
Environment: Step 8 - action: east  position: ( 4 , 3 )
Environment: Step 9 - action: north  position: ( 5 , 3 )
Environment: Step 10 - action: west  position: ( 5 , 2 )
Environment: Step 11 - action: north  position: ( 4 , 2 )
Environment: Step 12 - action: suck  position: ( 4 , 1 )
Environment: Step 13 - action: already clean - stay in position  position: ( 4 , 1 )
Environment: Step 14 - action: east  position: ( 4 , 1 )
En

Environment: Step 157 - action: east  position: ( 0 , 1 )
Environment: Step 158 - action: north  position: ( 1 , 1 )
Environment: Step 159 - action: north  position: ( 1 , 0 )
Environment: Step 160 - action: north  position: ( 1 , 0 )
Environment: Step 161 - action: already clean - stay in position  position: ( 1 , 0 )
Environment: Step 162 - action: north  position: ( 1 , 0 )
Environment: Step 163 - action: already clean - stay in position  position: ( 1 , 0 )
Environment: Step 164 - action: west  position: ( 1 , 0 )
Environment: Step 165 - action: east  position: ( 0 , 0 )
Environment: Step 166 - action: already clean - stay in position  position: ( 1 , 0 )
Environment: Step 167 - action: east  position: ( 1 , 0 )
Environment: Step 168 - action: east  position: ( 2 , 0 )
Environment: Step 169 - action: north  position: ( 3 , 0 )
Environment: Step 170 - action: south  position: ( 3 , 0 )
Environment: Step 171 - action: south  position: ( 3 , 1 )
Environment: Step 172 - action: already

Environment: Step 379 - action: north  position: ( 7 , 7 )
Environment: Step 380 - action: west  position: ( 7 , 6 )
Environment: Step 381 - action: south  position: ( 6 , 6 )
Environment: Step 382 - action: suck  position: ( 6 , 7 )
Environment: Step 383 - action: already clean - stay in position  position: ( 6 , 7 )
Environment: Step 384 - action: west  position: ( 6 , 7 )
Environment: Step 385 - action: west  position: ( 5 , 7 )
Environment: Step 386 - action: north  position: ( 4 , 7 )
Environment: Step 387 - action: south  position: ( 4 , 6 )
Environment: Step 388 - action: west  position: ( 4 , 7 )
Environment: Step 389 - action: west  position: ( 3 , 7 )
Environment: Step 390 - action: south  position: ( 2 , 7 )
Environment: Step 391 - action: east  position: ( 2 , 8 )
Environment: Step 392 - action: south  position: ( 3 , 8 )
Environment: Step 393 - action: already clean - stay in position  position: ( 3 , 9 )
Environment: Step 394 - action: already clean - stay in position  po

Environment: Step 601 - action: already clean - stay in position  position: ( 0 , 6 )
Environment: Step 602 - action: east  position: ( 0 , 6 )
Environment: Step 603 - action: north  position: ( 1 , 6 )
Environment: Step 604 - action: east  position: ( 1 , 5 )
Environment: Step 605 - action: north  position: ( 2 , 5 )
Environment: Step 606 - action: west  position: ( 2 , 4 )
Environment: Step 607 - action: east  position: ( 1 , 4 )
Environment: Step 608 - action: east  position: ( 2 , 4 )
Environment: Step 609 - action: east  position: ( 3 , 4 )
Environment: Step 610 - action: east  position: ( 4 , 4 )
Environment: Step 611 - action: west  position: ( 5 , 4 )
Environment: Step 612 - action: west  position: ( 4 , 4 )
Environment: Step 613 - action: already clean - stay in position  position: ( 3 , 4 )
Environment: Step 614 - action: south  position: ( 3 , 4 )
Environment: Step 615 - action: north  position: ( 3 , 5 )
Environment: Step 616 - action: west  position: ( 3 , 4 )
Environment:

Environment: Step 823 - action: already clean - stay in position  position: ( 1 , 6 )
Environment: Step 824 - action: already clean - stay in position  position: ( 1 , 6 )
Environment: Step 825 - action: already clean - stay in position  position: ( 1 , 6 )
Environment: Step 826 - action: east  position: ( 1 , 6 )
Environment: Step 827 - action: west  position: ( 2 , 6 )
Environment: Step 828 - action: west  position: ( 1 , 6 )
Environment: Step 829 - action: west  position: ( 0 , 6 )
Environment: Step 830 - action: already clean - stay in position  position: ( 0 , 6 )
Environment: Step 831 - action: east  position: ( 0 , 6 )
Environment: Step 832 - action: south  position: ( 1 , 6 )
Environment: Step 833 - action: west  position: ( 1 , 7 )
Environment: Step 834 - action: north  position: ( 0 , 7 )
Environment: Step 835 - action: north  position: ( 0 , 6 )
Environment: Step 836 - action: east  position: ( 0 , 5 )
Environment: Step 837 - action: south  position: ( 1 , 5 )
Environment: S

...

Environment: Step 85715 - action: west  position: ( 6 , 1 )
Environment: Step 85716 - action: north  position: ( 5 , 1 )
	Agent: Hit the north wall, will move away now...
Environment: Step 85717 - action: south  position: ( 5 , 0 )
Environment: Step 85718 - action: east  position: ( 5 , 1 )
Environment: Step 85719 - action: north  position: ( 6 , 1 )
	Agent: Hit the north wall, will move away now...
Environment: Step 85720 - action: south  position: ( 6 , 0 )
Environment: Step 85721 - action: west  position: ( 6 , 1 )
Environment: Step 85722 - action: west  position: ( 5 , 1 )
Environment: Step 85723 - action: north  position: ( 4 , 1 )
	Agent: Hit the north wall, will move away now...
Environment: Step 85724 - action: south  position: ( 4 , 0 )
Environment: Step 85725 - action: north  position: ( 4 , 1 )
	Agent: Hit the north wall, will move away now...
Environment: Step 85726 - action: south  position: ( 4 , 0 )
Environment: Step 85727 - action: north  position: ( 4 , 1 )
	Agent: Hit

Environment: Step 85935 - action: already clean - stay in position  position: ( 6 , 2 )
Environment: Step 85936 - action: already clean - stay in position  position: ( 6 , 2 )
Environment: Step 85937 - action: south  position: ( 6 , 2 )
Environment: Step 85938 - action: south  position: ( 6 , 3 )
Environment: Step 85939 - action: north  position: ( 6 , 4 )
Environment: Step 85940 - action: west  position: ( 6 , 3 )
Environment: Step 85941 - action: north  position: ( 5 , 3 )
Environment: Step 85942 - action: north  position: ( 5 , 2 )
Environment: Step 85943 - action: east  position: ( 5 , 1 )
Environment: Step 85944 - action: already clean - stay in position  position: ( 6 , 1 )
Environment: Step 85945 - action: west  position: ( 6 , 1 )
Environment: Step 85946 - action: west  position: ( 5 , 1 )
Environment: Step 85947 - action: south  position: ( 4 , 1 )
Environment: Step 85948 - action: east  position: ( 4 , 2 )
Environment: Step 85949 - action: west  position: ( 5 , 2 )
Environmen

Environment: Step 86154 - action: south  position: ( 5 , 5 )
Environment: Step 86155 - action: south  position: ( 5 , 6 )
Environment: Step 86156 - action: already clean - stay in position  position: ( 5 , 7 )
Environment: Step 86157 - action: east  position: ( 5 , 7 )
Environment: Step 86158 - action: east  position: ( 6 , 7 )
Environment: Step 86159 - action: east  position: ( 7 , 7 )
Environment: Step 86160 - action: south  position: ( 8 , 7 )
Environment: Step 86161 - action: already clean - stay in position  position: ( 8 , 8 )
Environment: Step 86162 - action: east  position: ( 8 , 8 )
	Agent: Hit the east wall, will move away now...
Environment: Step 86163 - action: west  position: ( 9 , 8 )
Environment: Step 86164 - action: north  position: ( 8 , 8 )
Environment: Step 86165 - action: south  position: ( 8 , 7 )
Environment: Step 86166 - action: east  position: ( 8 , 8 )
	Agent: Hit the east wall, will move away now...
Environment: Step 86167 - action: west  position: ( 9 , 8 )
E

Environment: Step 86375 - action: south  position: ( 7 , 5 )
Environment: Step 86376 - action: west  position: ( 7 , 6 )
Environment: Step 86377 - action: east  position: ( 6 , 6 )
Environment: Step 86378 - action: north  position: ( 7 , 6 )
Environment: Step 86379 - action: north  position: ( 7 , 5 )
Environment: Step 86380 - action: east  position: ( 7 , 4 )
Environment: Step 86381 - action: south  position: ( 8 , 4 )
Environment: Step 86382 - action: west  position: ( 8 , 5 )
Environment: Step 86383 - action: east  position: ( 7 , 5 )
Environment: Step 86384 - action: north  position: ( 8 , 5 )
Environment: Step 86385 - action: north  position: ( 8 , 4 )
Environment: Step 86386 - action: east  position: ( 8 , 3 )
	Agent: Hit the east wall, will move away now...
Environment: Step 86387 - action: west  position: ( 9 , 3 )
Environment: Step 86388 - action: north  position: ( 8 , 3 )
Environment: Step 86389 - action: south  position: ( 8 , 2 )
Environment: Step 86390 - action: north  po

Environment: Step 86595 - action: west  position: ( 5 , 3 )
Environment: Step 86596 - action: west  position: ( 4 , 3 )
Environment: Step 86597 - action: east  position: ( 3 , 3 )
Environment: Step 86598 - action: north  position: ( 4 , 3 )
Environment: Step 86599 - action: south  position: ( 4 , 2 )
Environment: Step 86600 - action: east  position: ( 4 , 3 )
Environment: Step 86601 - action: already clean - stay in position  position: ( 5 , 3 )
Environment: Step 86602 - action: west  position: ( 5 , 3 )
Environment: Step 86603 - action: east  position: ( 4 , 3 )
Environment: Step 86604 - action: west  position: ( 5 , 3 )
Environment: Step 86605 - action: west  position: ( 4 , 3 )
Environment: Step 86606 - action: already clean - stay in position  position: ( 3 , 3 )
Environment: Step 86607 - action: south  position: ( 3 , 3 )
Environment: Step 86608 - action: east  position: ( 3 , 4 )
Environment: Step 86609 - action: west  position: ( 4 , 4 )
Environment: Step 86610 - action: north  

In [ ]:
d_srandom = {}
d_sreflex = {}
d_mreflex = {}

for tuple in simple_random:
    key,val = tuple
    d_srandom.setdefault(key, []).append(val)
for tuple in simple_reflex:
    key,val = tuple
    d_sreflex.setdefault(key, []).append(val)
for tuple in model_reflex:
    key,val = tuple
    d_mreflex.setdefault(key, []).append(val)

    
print("Simple Randomized Agent Results: ")
for name, values in d_srandom.items():
    print("\t{name} {avg}".format(name=name, avg=sum(values)/len(values)))
    
print("Simple Reflex Agent Results: ")
for name, values in d_sreflex.items():
    print("\t{name} {avg}".format(name=name, avg=sum(values)/len(values)))
    
print("Model-based Reflex Agent Results: ")
for name, values in d_mreflex.items():
    print("\t{name} {avg}".format(name=name, avg=sum(values)/len(values)))

Fill out the following table with the average performance measure for 100 random runs (you may also create this table with code):

| Size     | Randomized Agent | Simple Reflex Agent | Model-based Reflex Agent |
|----------|------------------|---------------------|--------------------------|
| 5x5     | | | |
| 10x10   | | | |
| 100x100 | | | |

Add charts to compare the performance of the different agents.

In [ ]:
simple_random_transposed = simple_random.T
simple_reflex_transposed = simple_reflex.T
model_reflex_transposed = model_reflex.T

x, y_simple = simple_random_transposed
x1, y_reflex = simple_reflex_transposed
x2, y_model = model_reflex_transposed

plt.plot(x, reflex, label='Simple Random Agent')
plt.plot(x1, y_reflex, label='Simple Reflex Agent')
plt.plot(x2, y_model, label= "Model Reflex Agent")

In [ ]:
# Your graphs and discussion of the results goes here

## Task 5: Robustness of the agent implementations [10 Points] 

Describe how **your agent implementations** will perform 

* if it is put into a rectangular room with unknown size, 
* if the cleaning area can have an iregular shape (e.g., a hallway connecting two rooms), or 
* if the room contains obstacles (i.e., squares that it cannot pass through and trigger the bumper sensors).

In [ ]:
# Answer goes here
# https://www.explainthatstuff.com/how-roomba-works.html
# Roombas work by wall following and wall bouncing (aka randomly cleaning until an object is hit...)

## Graduate student advanced task: Obstacles [10 Points]

__Undergraduate students:__ This is a bonus task you can attempt if you like [+5 Bonus Points].

1. Change your simulation environment tor run experiments for the following problem: Add random obstacle squares that also trigger the bumper sensor. The agent does not know where the obstacles are. Observe how this changes the performance of the three implementations.

2. Describe what would need to be done to perform better with obstacles. Add code if you can. 

In [ ]:
# Your code and discussion goes here

## More advanced implementation tasks

* __Agent for and environment with obstacles:__ Implement an agent for an environment where the agent does not know how large the environment is (we assume it is rectangular), where it starts or where the obstacles are. An option would be to always move to the closest unchecked/uncleaned square (note that this is actualy depth-first search).

* __Utility-based agent:__ Change the environment for a $5 \times 5$ room, so each square has a fixed probability of getting dirty again. For the implementation, we give the environment a 2-dimensional array of probabilities. The utility of a state is defined as the number of currebntly clean squares in the room. Implement a utility-based agent that maximizes the expected utility over one full charge which lasts for 100000 time steps. To do this, the agent needs to learn the probabilities with which different squares get dirty again. This is very tricky!

In [ ]:
# Your ideas/code